Other resources:
 - [Other people using Yelp data](https://blog.michaelckennedy.net/2017/06/21/yelp-reviews-authorship-attribution-with-python-and-scikit-learn/)

In [79]:
import numpy as np
import pandas as pd
from scipy import sparse

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import accuracy_score
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression

pd.set_option("display.max_rows", None)


# 0. Load and Clean Data

We will concatenate the CSVs (instead of joining raw data) to cut down on RAM compute needs.

In [ ]:
def run_yelp_exp_prep(source_dir, min_yr, max_yr):
    '''
    Takes in directory of data sources csv files and outputs formatted X, Y for model training.
    '''
    
    df = pd.DataFrame()

    for yr in yr_range:
        #/Users/rajiinio/Documents/more-data-more-problems/mdmp_data_clean/2005_2004_final_dd.csv
        source_file = "/%d_%d_final_dd.csv" %(yr+1, yr)
        source_path = source_dir+source_file
        df_yr = pd.read_csv(source_path)
    
        #clean up
        df_yr["year"] = yr
    
        #TO DO: properly clean categories 
        #df_yr['categories_lst'] = df_yr['categories'].apply(lambda x: x.split(', '))
        df = df.append(df_yr)
        #df = pd.concat([df, df_yr])
    
    
    tab_cols = ['stars_x','useful', 'funny', 'cool']

    vec = TfidfVectorizer()
    X_text_vec = vec.fit_transform(df['text']).tocsr()
    X_tab = df[tab_cols].values
    X_tab = X_tab.astype(float)
    #X = sparse.hstack((X_text_vec, X_tab)).tocsr()
    X = sparse.hstack((X_text_vec, X_tab)).tocsr()

    y = (df['stars_y'].values >= 3.).astype(int)
    
    
    return X, y

In [89]:
#df1 = pd.read_csv('yelp/2006_2005_final_dd.csv')
#df2 = pd.read_csv('yelp/2007_2006_final_dd.csv')

source_dir = "/Users/rajiinio/Documents/more-data-more-problems/mdmp_data_clean"
min_yr = 2004#2004
max_yr = 2006#2023
yr_range = list(range(min_yr, max_yr+1))

df = pd.DataFrame()

for yr in yr_range:
    #/Users/rajiinio/Documents/more-data-more-problems/mdmp_data_clean/2005_2004_final_dd.csv
    source_file = "/%d_%d_final_dd.csv" %(yr+1, yr)
    source_path = source_dir+source_file
    df_yr = pd.read_csv(source_path)
    
    #clean up
    df_yr["year"] = yr
    
    #TO DO: properly clean categories 
    #df_yr['categories_lst'] = df_yr['categories'].apply(lambda x: x.split(', '))
    df = df.append(df_yr)
    #df = pd.concat([df, df_yr])
    

In [81]:
df = df.sort_values('year') 

#This should be happening anyways (because of how we concat) but do this to make sure years are indexed in order

In [82]:
#df1['year'] = 2006
#df2['year'] = 2007

#df = pd.concat([df1,df2])

In [90]:
#print(df1.shape)
#print(df2.shape)

print(df.shape)

df

(4707, 22)


Unnamed: 0  stars_x useful funny cool  \
0             0      2.0      3     3    4   
1             1      4.0      0     0    0   
2             2      2.0      2     0    0   
3             3      3.0      4     0    0   
4             4      5.0      0     0    0   
5             5      5.0      1     0    1   
6             6      3.0      0     0    0   
7             7      3.0      0     0    0   
8             8      4.0      0     0    1   
9             9      4.0      0     0    1   
10           10      3.0      0     0    0   
11           11      5.0      2     1    1   
12           12      4.0      0     0    0   
13           13      4.0      0     0    0   
14           14      3.0      1     0    0   
15           15      5.0      0     0    0   
16           16      4.0      0     0    0   
17           17      4.0      0     0    0   
18           18      4.0      0     2    0   
19           19      5.0      0     0    0   
20           20      5.0      0     0    0   
21           21      5.0      1     0    0   
22           22      5.0      0     0    1   
23           23      3.0      1     0    1   
24           24      4.0      0     0    0   
25           25      5.0      1     0    0   
26           26      1.0      0     0    0   
27           27      4.0      4     0    0   
28           28      1.0      0     1    0   
29           29      5.0      1     0    0   
30           30      4.0      2     1    0   
31           31      4.0      1     0    0   
32           32      5.0      3     2    1   
33           33      3.0      0     0    0   
34           34      4.0      0     1    0   
35           35      5.0      2     2    2   
36           36      3.0      1     0    1   
37           37      4.0      0     0    0   
38           38      5.0      1     1    1   
39           39      4.0      1     1    0   
40           40      5.0      2     1    1   
41           41      5.0      2     0    0   
42           42      4.0      0     0    0   
43           43      5.0      1     0    0   
44           44      5.0      0     0    0   
45           45      3.0      0     0    0   
46           46      4.0      0     0    2   
47           47      5.0      6     0    3   
48           48      4.0      2     9    0   
49           49      4.0      2     3    0   
50           50      4.0      0     2    0   
51           51      5.0      3     1    1   
52           52      4.0      1     0    2   
53           53      5.0      1     0    0   
54           54      3.0      0     0    0   
55           55      4.0      1     0    0   
56           56      4.0      0     0    0   
57           57      4.0      1     0    0   
58           58      2.0      2     0    0   
59           59      4.0      2     0    0   
60           60      4.0      3     0    0   
61           61      5.0      0     0    0   
62           62      3.0      0     1    0   
63           63      4.0      3     0    1   
64           64      5.0      0     0    0   
65           65      4.0      1     0    1   
66           66      4.0      0     1    1   
67           67      4.0      1     1    1   
68           68      2.0      5     0    0   
69           69      4.0      0     0    0   
70           70      3.0      0     1    0   
71           71      4.0      1     0    0   
72           72      3.0      1     0    0   
73           73      2.0      6     4    1   
74           74      4.0      0     0    0   
75           75      5.0      0     1    2   
76           76      5.0      5     0    2   
77           77      5.0      1     0    2   
78           78      4.0      0     1    1   
79           79      4.0      0     0    0   
80           80      2.0      1     3    2   
81           81      4.0      1     0    1   
82           82      4.0      1     0    0   
83           83      5.0      0     0    1   
84           84      5.0      3     2    2   
85           85      5.0      0     0    0   
86 

In [38]:
#df.shape

In [39]:
# df1 = df1.sort_values('date')
# df2 = df2.sort_values('date')

In [40]:
# df['slice'] -> ['2006', '2007']

In [41]:
# df2.head()

In [42]:
#df1['categories_lst'] = df1['categories'].apply(lambda x: x.split(', '))

In [43]:
# How do we encode groups?

#TO DO: encode subgroups

ethnic_categories = [
'American (Traditional)',
    'American (New)',
    'Italian',
    'Mexican',
    'Japanese',
    'Chinese',
    'Southern',
    'Vietnamese',
    'Asian Fusion',
    'Mediterranean',
    'Thai'
]

# TODO: figure out how this works in the eval step
def is_subgroup(s,category):
    return category in row[s]

Copied from [this Jupyter notebook](https://github.com/ahegel/yelp-dataset/blob/master/Predicting%20Star%20Ratings.ipynb) but couldn't get it working

In [44]:
# TODO: Add categories and attributes

# df1['categories_clean'] = map(lambda x: '|'.join(x), df1['categories'])
# df1 = df1.categories_clean.str.get_dummies(sep='|')
# # merge
# # business_df = business_df.merge(categories_df, left_index=True, right_index=True)
# # remove intermediate columns (no longer needed)
# df1.drop(['categories', 'categories_clean'], axis=1, inplace=True)
# df1.head()


In [45]:
# business_df = business_df.join(pd.DataFrame(business_df['attributes'].to_dict()).T)
# # further split sub-attributes into their own columns
# cols_to_split = ['BusinessParking', 'Ambience', 'BestNights', 'GoodForMeal', 'HairSpecializesIn', 'Music']
# for col_to_split in cols_to_split:
#     new_df = pd.DataFrame(business_df[col_to_split].to_dict()).T
#     new_df.columns = [col_to_split + '_' + str(col) for col in new_df.columns]
#     business_df = business_df.join(new_df)

# business_df.drop(['attributes'] + cols_to_split, axis=1, inplace=True)
# business_df.head()


In [93]:
print(X_text_vec.shape)

print(X_tab.shape)
#print(X_text_vec, X_tab)

X = df[tab_cols].values
X.astype(float)

(4707, 20205)
(4707, 4)


array([[2., 3., 3., 4.],
       [4., 0., 0., 0.],
       [2., 2., 0., 0.],
       ...,
       [3., 2., 0., 2.],
       [2., 1., 0., 0.],
       [1., 1., 8., 1.]])

In [94]:
X_text_vec

<4707x20205 sparse matrix of type '<class 'numpy.float64'>'
	with 305060 stored elements in Compressed Sparse Row format>

In [95]:

tab_cols = ['stars_x','useful', 'funny', 'cool']

vec = TfidfVectorizer()
X_text_vec = vec.fit_transform(df['text']).tocsr()
X_tab = df[tab_cols].values
X_tab = X_tab.astype(float)
#X = sparse.hstack((X_text_vec, X_tab)).tocsr()
X = sparse.hstack((X_text_vec, X_tab)).tocsr()

y = (df['stars_y'].values >= 3.).astype(int)


#sparse.hstack(X, A) # error
#sparse.hstack(X.astype(object), A) # cast X to object; return object
#sparse.hstack(X, A.astype(float)) # cast A to float; return float
#hstack(X.A, A) # make X dense, result will be type object


#tab_cols = ['stars_x','useful', 'funny', 'cool']

#vec = TfidfVectorizer()
##X_text_vec = vec.fit_transform(df['text']).tocsr()
#X_tab = df[tab_cols].values
#X = sparse.hstack((X_text_vec, X_tab)).tocsr()

#y = (df['stars_y'].values >= 3.).astype(int)

# 1. Modeling!

In [ ]:
# for S1: subsample N from 0 to 1000; train on that and report test perf
# 
# add S2 and learn for S1 + S2[:100], S1 + S2[:200]
# continue for all slices

## 1.1 Using actual Yelp dates

In [105]:
#df.shape

(4707, 22)

In [93]:
#print(df1.shape, df2.shape)
#print(854+3853)

(854, 22) (3853, 21)
4707


In [92]:
#np.linspace(0, 854,4)

array([  0.        , 284.66666667, 569.33333333, 854.        ])

In [91]:
#np.linspace(854,4707,4)

array([ 854.        , 2138.33333333, 3422.66666667, 4707.        ])

In [94]:
#np.arange(0,4707,250)

array([   0,  250,  500,  750, 1000, 1250, 1500, 1750, 2000, 2250, 2500,
       2750, 3000, 3250, 3500, 3750, 4000, 4250, 4500])

In [97]:
year_counts_dict = df['year'].value_counts().to_dict()
year_counts_dict

year_idx_dict = {year: np.where(df['year'].values == year)[0] for year in df['year'].unique()}

In [98]:
#num = 900
#ignore_idx = [0,4,2,100]
#year_idx_dict_ignore = {k:[i for i in v if i not in ignore_idx] for k,v in year_idx_dict.items()}

In [99]:
# within avail idx, within year, then sample
# train_set_idx = []





def get_avail_idx(num, year_idx_dict, ignore_idx, avail_years):
    """
    input:
     - num: int of samples needed
     - year_idx_dict: dict of {year: list of idx} for the df
     - ignore_idx: list of idx to ignore
     - avail_years: list of years that are considered
    
    output:
     - avail_dict: dict of {num to sample: list of valid idx}
    """
    year_idx_dict_ignore = {k:[i for i in v if i not in ignore_idx] for k,v in year_idx_dict.items()}
    avail_dict = {}
    remaining = num
    for year in sorted(year_idx_dict_ignore.keys()):
        if remaining > 0:
            avail_year_idx = year_idx_dict_ignore[year]
            avail_year_num_idx = len(avail_year_idx)
            
            use_this_year = min(remaining, avail_year_num_idx)
            avail_dict[use_this_year] = avail_year_idx
            remaining -= avail_year_num_idx
    return avail_dict

def get_sample_avail_idx(avail_dict):
    avail_idx_lst = list()
    
    for num_to_sample, lst_to_sample in avail_dict.items():
        sample_idx = np.random.choice(lst_to_sample, size=num_to_sample, replace=False)
        avail_idx_lst.append(sample_idx)
        
    avail_idx = np.concatenate(avail_idx_lst)
    return avail_idx

In [100]:
#test = get_avail_idx(1000, year_idx_dict, [0,1,100],avail_years=[2006,2007])
#test.keys()

In [101]:
#type(X)

In [102]:
# held out set of 20% test
# train_size = 100, 200, 300, 400, 500, 600 (4 chunks)

# reference test_set = 100 random points from latest slice
# generalized test_set = 100 random points from total dataset
# source test_set = 100 random points from each training run

test_set_size = 100
N = df.shape[0]

# ref: take 100 from df
max_year = max(df['year'].values)
ref_test_idx = np.random.choice(year_idx_dict[max_year], size=test_set_size, replace=False)

# gen: take 100 from df1 and df2
gen_test_idx = np.random.choice(range(N), size=test_set_size, replace=False)


step_size = 250




for train_N in [2000]:
# for train_N in np.arange(step_size, N,step_size):
    ignore_idx = np.concatenate((ref_test_idx,gen_test_idx))
    total_idx_sample_dict = get_avail_idx(train_N+test_set_size, year_idx_dict, ignore_idx, avail_years=[2006, 2007])
    total_idx = get_sample_avail_idx(total_idx_sample_dict)
    
    train_idx = total_idx[test_set_size:]
    
    # source: take 100 from each train run
    source_test_idx = total_idx[:test_set_size]
    
    X_train = X[train_idx].toarray()
    y_train = y[train_idx]
    
    X_source, y_source = X[source_test_idx].toarray(), y[source_test_idx]
    X_ref, y_ref = X[ref_test_idx].toarray(), y[ref_test_idx]
    X_gen, y_gen = X[gen_test_idx].toarray(), y[gen_test_idx]
    
    model = make_pipeline(StandardScaler(), LogisticRegression())
    model.fit(X_train, y_train)

    yhat_source = model.predict(X_source)
    yhat_ref = model.predict(X_ref)
    yhat_gen = model.predict(X_gen)
    
    acc_source = accuracy_score(yhat_source, y_source)
    acc_ref = accuracy_score(yhat_ref, y_ref)
    acc_gen = accuracy_score(yhat_gen, y_gen)
    
    results = {
        'acc_source': acc_source,
        'acc_ref': acc_ref,
        'acc_gen': acc_gen,
        'source_test_idx': source_test_idx,
        'gen_test_idx': gen_test_idx,
        'ref_test_idx': ref_test_idx,
        'yhat_source': yhat_source,
        'yhat_ref': yhat_ref,
        'yhat_gen': yhat_gen,
        'y_source': y_source,
        'y_ref': y_ref,
        'y_gen': y_gen
    }
    

In [103]:
print(acc_source, acc_ref, acc_gen)

0.94 0.91 0.94


## 1.2 Using subsampled random slices